# Poro34B Lora fine-tuning with S-Group's data - 2 Q/A

In [ ]:
# This script finetunes the Poro34B model with 1 Question and Answer pair

## Initialization

In [1]:
!pip install peft

In [2]:
import torch
import json
from transformers import AutoModelForCausalLM, AutoTokenizer 
from transformers import TrainingArguments, Trainer
from transformers import pipeline
from peft import  get_peft_model, PromptTuningConfig, TaskType, PromptTuningInit
from datasets import load_dataset

2024-02-29 16:09:52.067525: I tensorflow/core/platform/cpu_feature_guard.cc:182] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: SSE4.1 SSE4.2 AVX AVX2 AVX512F FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.


In [3]:
device = torch.device("cuda") if torch.cuda.is_available() else torch.device("cpu")

In [4]:
print(device)

cpu


## Foundation model import

In [3]:
model_name='LumiOpen/Poro-34B'

In [4]:
tokenizer = AutoTokenizer.from_pretrained(model_name)

In [ ]:
branch = "1000B"
model = AutoModelForCausalLM.from_pretrained(model_name,
    torch_dtype=torch.bfloat16,
    revision=branch,
)

Loading checkpoint shards:   0%|          | 0/14 [00:00<?, ?it/s]

## Setting up the Lora parameters

In [8]:
from peft import LoraConfig, get_peft_model

In [9]:
config = LoraConfig(
    r=8,
    lora_alpha=8,
    target_modules=["query_key_value"],
    lora_dropout=0.05,
    bias="none",
    task_type="CAUSAL_LM"
)

In [10]:
peft_model = get_peft_model(model, config)

In [11]:
trainable_params = 0
all_param = 0

# iterating over all parameters
for _, param in peft_model.named_parameters():
    # adding parameters to total
    all_param += param.numel()
    # adding parameters to trainable if they require a graident
    if param.requires_grad:
        trainable_params += param.numel()

# print number of trainable parameters
print(f"trainable params: {trainable_params}")
print(f"all params: {all_param}")
print(f"trainable: {100 * trainable_params / all_param:.2f}%")

trainable params: 12386304
all params: 34229336064
trainable: 0.04%


## Preparing the training data

In [12]:
# prepare the data for training
def prepare_train_data(data):
    text_input = data['text']
    tokenized_input = tokenizer(text_input, return_tensors='pt', padding=True)
    tokenized_input['labels'] = tokenized_input['input_ids']
    return tokenized_input

In [13]:
dataset = load_dataset("json", data_files="prompts_2.json")

Generating train split: 0 examples [00:00, ? examples/s]

In [14]:
train_dataset = dataset['train'].map(prepare_train_data, batched=True, remove_columns=["text"])

Map:   0%|          | 0/2 [00:00<?, ? examples/s]

## Setting up the training parameters

In [15]:
from transformers import DataCollatorForLanguageModeling

In [16]:
trainer = Trainer(
    model=peft_model,
    train_dataset=train_dataset,
    args=TrainingArguments(
        per_device_train_batch_size=4,
        gradient_accumulation_steps=4,
        warmup_steps=20,
        max_steps=20,
        learning_rate=1e-3,
        logging_steps=1,
        output_dir='outputs',
    ),
    data_collator=DataCollatorForLanguageModeling(tokenizer, mlm=False)
)

In [17]:
trainer.train()

/opt/conda/lib/python3.10/site-packages/transformers/optimization.py:411: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(
wandb: Currently logged in as: timo-au-laine. Use `wandb login --relogin` to force relogin


You're using a BloomTokenizerFast tokenizer. Please note that with a fast tokenizer, using the `__call__` method is faster than using a method to encode the text followed by a call to the `pad` method to get a padded encoding.


TrainOutput(global_step=20, training_loss=0.43031005859375, metrics={'train_runtime': 1884.4748, 'train_samples_per_second': 0.17, 'train_steps_per_second': 0.011, 'total_flos': 1415086626078720.0, 'train_loss': 0.43031005859375, 'epoch': 20.0})

## Saving the finetuned model

In [18]:
model_id2 = "Poro-34B-Lora-2"

In [19]:
peft_model.save_pretrained(model_id2)

In [ ]:
!ls -lh {model_id2}

## Testing

In [ ]:
def generate_output(model, inputs, max_new_tokens=100):
    outputs = model.generate(
        input_ids=inputs["input_ids"],
        max_new_tokens=max_new_tokens,
        temperature=0.1,
    )
    return outputs

### Original model

In [ ]:
prompt = tokenizer('Given the question delimited by triple backticks ```{ Kuinka vaihdan uutiskirjeen sähköpostiosoitteen? }```, what is the answer? Answer:', return_tensors="pt")
result = generate_output(model,prompt)
print(tokenizer.batch_decode(result, skip_special_tokens=True))

['Given the question delimited by triple backticks ```{ Kuinka vaihdan uutiskirjeen sähköpostiosoitteen? }```, what is the answer? Answer: ```{ Voit vaihtaa uutiskirjeen sähköpostiosoitteen kirjautumalla sisään ja menemällä Oma tili -osioon. }```\n']


In [ ]:
prompt = tokenizer('Given the question delimited by triple backticks ```{ Miksi sähköpostiosoite tulee vahvistaa? }```, what is the answer? Answer:', return_tensors="pt")
result = generate_output(model,prompt)
print(tokenizer.batch_decode(result, skip_special_tokens=True))

['Given the question delimited by triple backticks ```{ Miksi sähköpostiosoite tulee vahvistaa? }```, what is the answer? Answer: Because the email address needs to be confirmed.']


### Finetuned model

In [23]:
from peft import PeftModel

In [24]:
loaded_model = PeftModel.from_pretrained(model,model_id2,is_trainable=False)

In [25]:
prompt = tokenizer('Given the question delimited by triple backticks ```{ Kuinka vaihdan uutiskirjeen sähköpostiosoitteen? }```, what is the answer? Answer:', return_tensors="pt")
result = generate_output(loaded_model,prompt)
print(tokenizer.batch_decode(result, skip_special_tokens=True))

['Given the question delimited by triple backticks ```{ Kuinka vaihdan uutiskirjeen sähköpostiosoitteen? }```, what is the answer? Answer: { Peruuta ensin vanhaan osoitteeseen tilattu uutiskirje kirjeen alareunan “Peruuta tilaus” -linkistä.\nTilaa uutiskirje uudelleen oikeaan osoitteeseen. }\n\n### Answering a Given Question\n\nGiven a question delimited by triple backticks ```{ Kuinka vaihdan uutiskirjeen sähköpostiosoitteen? }```, what is the answer? Answer: { Peruuta ensin vanhaan osoitteeseen tilattu uutiskirje kirjeen alareunan “Peruuta tilaus” -linkistä.\nTilaa uutiskirje uudelleen oikeaan osoitteeseen. }\n\n## Data Sources\n\nThe data for currently supported']


In [26]:
prompt = tokenizer('Given the question delimited by triple backticks ```{ Miksi sähköpostiosoite tulee vahvistaa? }```, what is the answer? Answer:', return_tensors="pt")
result = generate_output(loaded_model,prompt)
print(tokenizer.batch_decode(result, skip_special_tokens=True))

['Given the question delimited by triple backticks ```{ Miksi sähköpostiosoite tulee vahvistaa? }```, what is the answer? Answer: {Sähköpostiosoitteiden vahvistaminen on yleisesti käytössä oleva tapa varmistua siitä, että henkilöllä itsellään on pääsy hänen tiedoissaan olevaan sähköpostiosoitteeseen.\n\nSähköpostiosoite tulee vahvistaa itse, joko S-mobiilissa tai samalla kun luot itsellesi S-käyttäjätilin. Kun lähetät vahvistusviestin omissa tiedoissasi näkyvään sähköpostiosoitteeseen ja vahvistat itse osoitteen oikeaksi sähköpostiisi lähetetyllä vahvistuskoodilla, saamme varmistuksen, että osoitteesi on voimassa ja kuuluu juuri sinulle.\n\nJos asiakastiedoissasi olevasta sähköpostiosoitteesta puuttuu vielä vahvistus, näkyy']
